In [3]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
from flask import Flask, jsonify, render_template
import json

In [4]:
import sqlalchemy
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session
from sqlalchemy import create_engine, func
from sqlalchemy.ext.declarative import declarative_base
Base = declarative_base()

In [25]:
sba = "FOIA - 7(a)(FY2010-Present).xlsx"
sba_df = pd.read_excel(sba)
sba_df.head()

*Data as of 03/31/2018                     Unnamed: 1  \
0                Program                       BorrName   
1                     7A  CRESA PARTNERS - DENVER, INC.   
2                     7A             The Hilltop Tavern   
3                     7A        River City Car Wash LLC   
4                     7A                  Alphagraphics   

                      Unnamed: 2       Unnamed: 3 Unnamed: 4 Unnamed: 5  \
0                     BorrStreet         BorrCity  BorrState    BorrZip   
1  7979 E TUFTS AVE PKWY STE 810           DENVER         CO      80237   
2               4757 Folsom Blvd       Sacramento         CA      95819   
3                649 Harbor Blvd  West Sacramento         CA      95691   
4               71 Newtown Road.          Danbury         CT      06810   

                               Unnamed: 6         Unnamed: 7      Unnamed: 8  \
0                                BankName         BankStreet        BankCity   
1               Zions Bank, A Division of        1 S Main St  SALT LAKE CITY   
2                             Plumas Bank      336 W Main St          QUINCY   
3  Wells Fargo Bank, National Association  101 N Philips Ave     SIOUX FALLS   
4                      Union Savings Bank        226 Main St         DANBURY   

  Unnamed: 9      ...          Unnamed: 24   Unnamed: 25  \
0  BankState      ...        ProjectCounty  ProjectState   
1         UT      ...               DENVER            CO   
2         CA      ...           SACRAMENTO            CA   
3         SD      ...                 YOLO            CA   
4         CT      ...            FAIRFIELD            CT   

                    Unnamed: 26            Unnamed: 27   Unnamed: 28  \
0             SBADistrictOffice  CongressionalDistrict  BusinessType   
1     COLORADO DISTRICT OFFICE                      01   CORPORATION   
2   SACRAMENTO DISTRICT OFFICE                      06   CORPORATION   
3   SACRAMENTO DISTRICT OFFICE                      06   CORPORATION   
4  CONNECTICUT DISTRICT OFFICE                      05   CORPORATION   

  Unnamed: 29          Unnamed: 30           Unnamed: 31     Unnamed: 32  \
0  LoanStatus        ChargeOffDate  GrossChargeOffAmount  RevolverStatus   
1         PIF                  NaN                     0               1   
2      EXEMPT                  NaN                     0               0   
3      CHGOFF  2015-08-24 00:00:00                320098               0   
4      EXEMPT                  NaN                     0               1   

     Unnamed: 33  
0  JobsSupported  
1             35  
2              6  
3             27  
4              5  

[5 rows x 34 columns]

In [31]:
actual_cols = sba_df.loc[0]

sba_df.columns = actual_cols

In [36]:
sba_df = sba_df.loc[1:]

In [43]:
ls = [1,2,3,4,5]

ls[1:3]

[2, 3]

In [40]:
sba_df['ApprovalFiscalYear'].unique()

array(['2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017',
       '2018'], dtype=object)

In [24]:
sba_df['ApprovalFiscalYear'].unique()

array([ 2010.,  2011.,  2012.,  2013.,  2014.,  2015.,    nan])

In [44]:
# Create engine using the `clean_measurement.sqlite` database file
engine = create_engine('sqlite:///sbc_FY2010-Present.sqlite')

In [45]:
sba_df.to_sql("bank_data", engine, index=False, if_exists="replace" )

In [47]:
conn = engine.connect()

In [48]:
results = conn.execute("select * from bank_data limit 10").fetchall()

In [49]:
bank_df = pd.read_sql("select distinct BankName from bank_data", conn)
bank_df.to_json(orient='records')

'[{"BankName":"Zions Bank, A Division of"},{"BankName":"Plumas Bank"},{"BankName":"Wells Fargo Bank, National Association"},{"BankName":"Union Savings Bank"},{"BankName":"Crossroads Small Business Solutions, LLC"},{"BankName":"Lake Region Bank"},{"BankName":"Bank of Hope"},{"BankName":"Pacoima Development FCU"},{"BankName":"First National Community Bank"},{"BankName":"Renasant Bank"},{"BankName":"Scotiabank de Puerto Rico"},{"BankName":"The Citizens Bank"},{"BankName":"Austin County State Bank"},{"BankName":"North Shore Bank, A Cooperative Bank"},{"BankName":"Lower East Side People\'s FCU"},{"BankName":"Seacoast Commerce Bank"},{"BankName":"First Colorado National Bank"},{"BankName":"Associated Bank, National Association"},{"BankName":"U.S. Bank National Association"},{"BankName":"Bank of Sullivan"},{"BankName":"JPMorgan Chase Bank, National Association"},{"BankName":"Citizens Bank, National Association"},{"BankName":"BMO Harris Bank National Association"},{"BankName":"BancorpSouth Ban

In [50]:
new_df = pd.read_sql("select ApprovalFiscalYear as fundingYear, sum(grossApproval) as grossApproval from bank_data group by 1", conn)

new_df.head(60)

fundingYear  grossApproval
0        2010    12475761191
1        2011    19803438294
2        2012    15393751573
3        2013    18132752131
4        2014    19464332397
5        2015    23913250154
6        2016    24428912339
7        2017    25648384195
8        2018    12635218213

In [9]:
from pprint import pprint
pprint (new_df.to_json(orient='records'))

('[{"BankName":"121 Financial '
 'CU","fundingYear":2011.0,"grossApproval":298000.0},{"BankName":"121 '
 'Financial '
 'CU","fundingYear":2012.0,"grossApproval":100000.0},{"BankName":"121 '
 'Financial '
 'CU","fundingYear":2013.0,"grossApproval":247000.0},{"BankName":"121 '
 'Financial '
 'CU","fundingYear":2014.0,"grossApproval":152000.0},{"BankName":"121 '
 'Financial '
 'CU","fundingYear":2015.0,"grossApproval":225000.0},{"BankName":"1880 '
 'Bank","fundingYear":2010.0,"grossApproval":1085000.0},{"BankName":"1880 '
 'Bank","fundingYear":2011.0,"grossApproval":1175000.0},{"BankName":"1880 '
 'Bank","fundingYear":2012.0,"grossApproval":500000.0},{"BankName":"1880 '
 'Bank","fundingYear":2014.0,"grossApproval":140000.0},{"BankName":"1st '
 'Advantage '
 'Bank","fundingYear":2014.0,"grossApproval":140000.0},{"BankName":"1st '
 'Bank","fundingYear":2010.0,"grossApproval":295000.0},{"BankName":"1st '
 'Bank","fundingYear":2011.0,"grossApproval":168000.0},{"BankName":"1st Bank '
 'Yuma","

 'Trust & Savings '
 'Bank","fundingYear":2011.0,"grossApproval":155000.0},{"BankName":"American '
 'Trust & Savings '
 'Bank","fundingYear":2012.0,"grossApproval":630000.0},{"BankName":"American '
 'Trust & Savings '
 'Bank","fundingYear":2013.0,"grossApproval":1025000.0},{"BankName":"American '
 'Trust & Savings '
 'Bank","fundingYear":2014.0,"grossApproval":740500.0},{"BankName":"American '
 'Trust & Savings '
 'Bank","fundingYear":2015.0,"grossApproval":350000.0},{"BankName":"American '
 'Trust '
 'Bank","fundingYear":2013.0,"grossApproval":750000.0},{"BankName":"American '
 'Trust '
 'Bank","fundingYear":2014.0,"grossApproval":5217100.0},{"BankName":"American '
 'United Family of Credit Unions '
 'FCU","fundingYear":2013.0,"grossApproval":4556556.0},{"BankName":"American '
 'United Family of Credit Unions '
 'FCU","fundingYear":2014.0,"grossApproval":600000.0},{"BankName":"AmericanTrust '
 'Federal Savings '
 'Bank","fundingYear":2010.0,"grossApproval":87500.0},{"BankName":"Americ

 'State '
 'Bank","fundingYear":2010.0,"grossApproval":11836000.0},{"BankName":"Beneficial '
 'State '
 'Bank","fundingYear":2011.0,"grossApproval":1616300.0},{"BankName":"Beneficial '
 'State '
 'Bank","fundingYear":2012.0,"grossApproval":2540100.0},{"BankName":"Beneficial '
 'State '
 'Bank","fundingYear":2013.0,"grossApproval":8927500.0},{"BankName":"Beneficial '
 'State '
 'Bank","fundingYear":2014.0,"grossApproval":1393000.0},{"BankName":"Beneficial '
 'State '
 'Bank","fundingYear":2015.0,"grossApproval":1994100.0},{"BankName":"Berkshire '
 'Bank","fundingYear":2010.0,"grossApproval":34063400.0},{"BankName":"Berkshire '
 'Bank","fundingYear":2011.0,"grossApproval":54423100.0},{"BankName":"Berkshire '
 'Bank","fundingYear":2012.0,"grossApproval":43141400.0},{"BankName":"Berkshire '
 'Bank","fundingYear":2013.0,"grossApproval":33194100.0},{"BankName":"Berkshire '
 'Bank","fundingYear":2014.0,"grossApproval":55529800.0},{"BankName":"Berkshire '
 'Bank","fundingYear":2015.0,"grossApp

 'Company","fundingYear":2015.0,"grossApproval":738269.0},{"BankName":"Clear '
 'Mountain '
 'Bank","fundingYear":2014.0,"grossApproval":947700.0},{"BankName":"Clear '
 'Mountain '
 'Bank","fundingYear":2015.0,"grossApproval":685000.0},{"BankName":"Clearview '
 'FCU","fundingYear":2010.0,"grossApproval":80000.0},{"BankName":"Clinton '
 'Bank","fundingYear":2014.0,"grossApproval":981500.0},{"BankName":"Clinton '
 'Savings '
 'Bank","fundingYear":2011.0,"grossApproval":1000000.0},{"BankName":"Clinton '
 'Savings '
 'Bank","fundingYear":2013.0,"grossApproval":1250000.0},{"BankName":"CoBiz '
 'Bank","fundingYear":2010.0,"grossApproval":22495100.0},{"BankName":"CoBiz '
 'Bank","fundingYear":2011.0,"grossApproval":42816800.0},{"BankName":"CoBiz '
 'Bank","fundingYear":2012.0,"grossApproval":18719000.0},{"BankName":"CoBiz '
 'Bank","fundingYear":2013.0,"grossApproval":15600100.0},{"BankName":"CoBiz '
 'Bank","fundingYear":2014.0,"grossApproval":58116100.0},{"BankName":"CoBiz '
 'Bank","fundin

 'Bank","fundingYear":2014.0,"grossApproval":838067.0},{"BankName":"Equitable '
 'Bank","fundingYear":2015.0,"grossApproval":784500.0},{"BankName":"Equity '
 'Bank","fundingYear":2010.0,"grossApproval":2392500.0},{"BankName":"Equity '
 'Bank","fundingYear":2011.0,"grossApproval":19002600.0},{"BankName":"Equity '
 'Bank","fundingYear":2012.0,"grossApproval":5822500.0},{"BankName":"Equity '
 'Bank","fundingYear":2013.0,"grossApproval":8319800.0},{"BankName":"Equity '
 'Bank","fundingYear":2014.0,"grossApproval":2580242.0},{"BankName":"Equity '
 'Bank","fundingYear":2015.0,"grossApproval":1265000.0},{"BankName":"Ericson '
 'State Bank","fundingYear":2011.0,"grossApproval":150000.0},{"BankName":"Erie '
 'FCU","fundingYear":2010.0,"grossApproval":72000.0},{"BankName":"Essential '
 'FCU","fundingYear":2010.0,"grossApproval":35400.0},{"BankName":"Essential '
 'FCU","fundingYear":2011.0,"grossApproval":820000.0},{"BankName":"Essex '
 'Bank","fundingYear":2010.0,"grossApproval":800000.0},{"Bank

...

 'Bank & '
 'Trust","fundingYear":2011.0,"grossApproval":120000.0},{"BankName":"Pioneer '
 'Bank & '
 'Trust","fundingYear":2012.0,"grossApproval":556000.0},{"BankName":"Pioneer '
 'Bank & '
 'Trust","fundingYear":2013.0,"grossApproval":228100.0},{"BankName":"Pioneer '
 'Bank & '
 'Trust","fundingYear":2015.0,"grossApproval":165800.0},{"BankName":"Pioneer '
 'Bank of '
 'Wisconsin","fundingYear":2013.0,"grossApproval":150000.0},{"BankName":"Pioneer '
 'Bank of '
 'Wisconsin","fundingYear":2014.0,"grossApproval":70000.0},{"BankName":"Pioneer '
 'Bank of '
 'Wisconsin","fundingYear":2015.0,"grossApproval":151200.0},{"BankName":"Pioneer '
 'Bank, '
 'SSB","fundingYear":2010.0,"grossApproval":8330000.0},{"BankName":"Pioneer '
 'Bank, '
 'SSB","fundingYear":2011.0,"grossApproval":10116500.0},{"BankName":"Pioneer '
 'Bank, '
 'SSB","fundingYear":2012.0,"grossApproval":12641700.0},{"BankName":"Pioneer '
 'Bank, '
 'SSB","fundingYear":2013.0,"grossApproval":14628900.0},{"BankName":"Pioneer '
 

 'CU","fundingYear":2011.0,"grossApproval":190000.0},{"BankName":"Self-Help '
 'CU","fundingYear":2013.0,"grossApproval":165000.0},{"BankName":"Self-Help '
 'CU","fundingYear":2014.0,"grossApproval":100000.0},{"BankName":"Self-Help '
 'CU","fundingYear":2015.0,"grossApproval":63100.0},{"BankName":"Self-Help '
 'FCU","fundingYear":2010.0,"grossApproval":2575200.0},{"BankName":"Self-Help '
 'FCU","fundingYear":2011.0,"grossApproval":190500.0},{"BankName":"Self-Help '
 'FCU","fundingYear":2015.0,"grossApproval":268000.0},{"BankName":"Sentry '
 'Bank","fundingYear":2010.0,"grossApproval":2234500.0},{"BankName":"Sentry '
 'Bank","fundingYear":2011.0,"grossApproval":1025000.0},{"BankName":"Sentry '
 'Bank","fundingYear":2012.0,"grossApproval":4345200.0},{"BankName":"Sentry '
 'Bank","fundingYear":2013.0,"grossApproval":4034000.0},{"BankName":"Sentry '
 'Bank","fundingYear":2014.0,"grossApproval":7291100.0},{"BankName":"Sentry '
 'Bank","fundingYear":2015.0,"grossApproval":399500.0},{"BankNam

 'Bank of Southside '
 'Virginia","fundingYear":2015.0,"grossApproval":50000.0},{"BankName":"The '
 'Bank of '
 'Tampa","fundingYear":2011.0,"grossApproval":330000.0},{"BankName":"The Bank '
 'of Tampa","fundingYear":2013.0,"grossApproval":286000.0},{"BankName":"The '
 'Bank of '
 'Tescott","fundingYear":2013.0,"grossApproval":350000.0},{"BankName":"The '
 'Bank of '
 'Tioga","fundingYear":2010.0,"grossApproval":250000.0},{"BankName":"The Bank '
 'of Vernon","fundingYear":2011.0,"grossApproval":2999000.0},{"BankName":"The '
 'Bank of '
 'Vernon","fundingYear":2013.0,"grossApproval":401400.0},{"BankName":"The Bank '
 'of '
 'Washington","fundingYear":2010.0,"grossApproval":365000.0},{"BankName":"The '
 'Bank of '
 'Washington","fundingYear":2011.0,"grossApproval":250000.0},{"BankName":"The '
 'Bank of '
 'Washington","fundingYear":2012.0,"grossApproval":563000.0},{"BankName":"The '
 'Bank of '
 'Washington","fundingYear":2014.0,"grossApproval":433000.0},{"BankName":"The '
 'Bank of '
 '

 'State Bank","fundingYear":2012.0,"grossApproval":1198000.0},{"BankName":"The '
 'Shelby State '
 'Bank","fundingYear":2013.0,"grossApproval":55000.0},{"BankName":"The Shelby '
 'State Bank","fundingYear":2014.0,"grossApproval":150000.0},{"BankName":"The '
 'Simsbury Bank & Trust Company, '
 'Inc.","fundingYear":2010.0,"grossApproval":250000.0},{"BankName":"The '
 'Simsbury Bank & Trust Company, '
 'Inc.","fundingYear":2011.0,"grossApproval":930000.0},{"BankName":"The '
 'Simsbury Bank & Trust Company, '
 'Inc.","fundingYear":2012.0,"grossApproval":608100.0},{"BankName":"The '
 'Simsbury Bank & Trust Company, '
 'Inc.","fundingYear":2013.0,"grossApproval":1412000.0},{"BankName":"The '
 'Simsbury Bank & Trust Company, '
 'Inc.","fundingYear":2014.0,"grossApproval":1989600.0},{"BankName":"The '
 'Simsbury Bank & Trust Company, '
 'Inc.","fundingYear":2015.0,"grossApproval":2704773.0},{"BankName":"The '
 'Southern Bank '
 'Company","fundingYear":2014.0,"grossApproval":1250000.0},{"BankNa

 'Bank & '
 'Trust","fundingYear":2013.0,"grossApproval":1314000.0},{"BankName":"Wayne '
 'Bank","fundingYear":2010.0,"grossApproval":925700.0},{"BankName":"Wayne '
 'Bank","fundingYear":2012.0,"grossApproval":435000.0},{"BankName":"Wayne Bank '
 'and Trust '
 'Co.","fundingYear":2010.0,"grossApproval":955000.0},{"BankName":"Wayne Bank '
 'and Trust '
 'Co.","fundingYear":2011.0,"grossApproval":105000.0},{"BankName":"Wayne Bank '
 'and Trust '
 'Co.","fundingYear":2012.0,"grossApproval":15000.0},{"BankName":"Wayne Bank '
 'and Trust '
 'Co.","fundingYear":2013.0,"grossApproval":774600.0},{"BankName":"Wayne Bank '
 'and Trust '
 'Co.","fundingYear":2014.0,"grossApproval":1025000.0},{"BankName":"Wayne Bank '
 'and Trust '
 'Co.","fundingYear":2015.0,"grossApproval":187600.0},{"BankName":"Wayne '
 'County '
 'Bank","fundingYear":2015.0,"grossApproval":95000.0},{"BankName":"Wayne '
 'Savings Community '
 'Bank","fundingYear":2010.0,"grossApproval":1000500.0},{"BankName":"Wayne '
 'Savings 

In [51]:
all_cols = pd.read_sql("select * from bank_data limit 10", conn)


In [52]:
all_cols.columns

Index(['Program', 'BorrName', 'BorrStreet', 'BorrCity', 'BorrState', 'BorrZip',
       'BankName', 'BankStreet', 'BankCity', 'BankState', 'BankZip',
       'GrossApproval', 'SBAGuaranteedApproval', 'ApprovalDate',
       'ApprovalFiscalYear', 'FirstDisbursementDate', 'DeliveryMethod',
       'subpgmdesc', 'InitialInterestRate', 'TermInMonths', 'NaicsCode',
       'NaicsDescription', 'FranchiseCode', 'FranchiseName', 'ProjectCounty',
       'ProjectState', 'SBADistrictOffice', 'CongressionalDistrict',
       'BusinessType', 'LoanStatus', 'ChargeOffDate', 'GrossChargeOffAmount',
       'RevolverStatus', 'JobsSupported'],
      dtype='object')

In [53]:
new_df2 = pd.read_sql("select NaicsDescription, NaicsCode, count(NaicsCode) sic_count from bank_data \
group by 1,2 order by sic_count desc limit 10", conn)
new_df2.head(n=10)

NaicsDescription NaicsCode  sic_count
0                           Full-Service Restaurants    722511      15860
1                        Limited-Service Restaurants    722513      10666
2                                Offices of Dentists    621210       9686
3                           Full-Service Restaurants    722110       8162
4  Offices of Physicians (except Mental Health Sp...    621111       7311
5           Hotels (except Casino Hotels) and Motels    721110       7192
6  General Freight Trucking, Long Distance, Truck...    484121       7049
7                               Landscaping Services    561730       6536
8                          General Automotive Repair    811111       6535
9              All Other Specialty Trade Contractors    238990       6533

In [13]:
from pprint import pprint
pprint (new_df2.to_json(orient='records'))

('[{"BankName":"The Huntington National Bank","SICDISCRIP":"General Freight '
 'Trucking, Long Distance, '
 'Truckload","SIC":484121.0,"sic_count":1976},{"BankName":"First Financial '
 'Bank","SICDISCRIP":"Broilers and Other Meat '
 'Type","SIC":112320.0,"sic_count":1434},{"BankName":"Live Oak Banking '
 'Company","SICDISCRIP":"Veterinary '
 'Services","SIC":541940.0,"sic_count":1149},{"BankName":"JPMorgan Chase Bank, '
 'National Association","SICDISCRIP":"Offices of Physicians (except Mental '
 'Health Specialists)","SIC":621111.0,"sic_count":988},{"BankName":"JPMorgan '
 'Chase Bank, National Association","SICDISCRIP":"Full-Service '
 'Restaurants","SIC":722110.0,"sic_count":783},{"BankName":"Live Oak Banking '
 'Company","SICDISCRIP":"Offices of '
 'Dentists","SIC":621210.0,"sic_count":757},{"BankName":"The Huntington '
 'National Bank","SICDISCRIP":"General Freight Trucking, '
 'Local","SIC":484110.0,"sic_count":723},{"BankName":"Live Oak Banking '
 'Company","SICDISCRIP":"Pharmac

In [54]:
all_cols.columns

Index(['Program', 'BorrName', 'BorrStreet', 'BorrCity', 'BorrState', 'BorrZip',
       'BankName', 'BankStreet', 'BankCity', 'BankState', 'BankZip',
       'GrossApproval', 'SBAGuaranteedApproval', 'ApprovalDate',
       'ApprovalFiscalYear', 'FirstDisbursementDate', 'DeliveryMethod',
       'subpgmdesc', 'InitialInterestRate', 'TermInMonths', 'NaicsCode',
       'NaicsDescription', 'FranchiseCode', 'FranchiseName', 'ProjectCounty',
       'ProjectState', 'SBADistrictOffice', 'CongressionalDistrict',
       'BusinessType', 'LoanStatus', 'ChargeOffDate', 'GrossChargeOffAmount',
       'RevolverStatus', 'JobsSupported'],
      dtype='object')

In [60]:
# new_df3 = pd.read_sql("select BankName, sum(GrossApproval) as TotalLoansApproval, ApprovalFiscalYear \
# from bank_data where BankName <> 'NONE' group by 1", conn)
# new_df3.head(n=10)


x = '''
select b.BankName
, b.ApprovalFiscalYear
, b.count_of_loans
, sum(case when chargeOffDate is null then 0 else 1 end) as charge_off_count

from bank_data a

inner join (
    
    select BankName
    , ApprovalFiscalYear
    , count(BorrName) count_of_loans

    from bank_data

    group by 1,2
) b
on a.BankName = b.BankName
and a.ApprovalFiscalYear = b.ApprovalFiscalYear

group by 1,2,3

'''

SyntaxError: invalid syntax (<ipython-input-60-b797cdf13910>, line 6)

In [59]:
x

'\nselect b.BankName\n, b.ApprovalFiscalYear\n, b.count_of_loans\n, sum(case when chargeOffDate is null then 0 else 1 end) as charge_off_count\n\nfrom bank_data a\n\ninner join (\n    \n    select BankName\n    , ApprovalFiscalYear\n    , count(BorrName) count_of_loans\n\n    from bank_data\n\n    group by 1,2\n) b\non a.BankName = b.BankName\nand a.ApprovalFiscalYear = b.ApprovalFiscalYear\n\ngroup by 1,2,3\n\n'

In [16]:
new_df3b = pd.read_sql("select BankName, BorrName, sum(GrossChargeOffAmount) as GrossChargeOff, ChargeOffDate \
from bank_data where GrossChargeOffAmount >1 group by 2,4", conn)

new_df3b.head(n=10)

BankName                        BorrName  \
0                                Umpqua Bank  (L/D) Max Aviation Safety Grou   
1                        Integrity Bank, ssb            1 GREEN STREET, INC.   
2       Santander Bank, National Association          1-5 Cadman Plaza, Inc.   
3  JPMorgan Chase Bank, National Association                 1-800-Got-Junk?   
4        Union National Bank & Trust Company          10-2 Distributors, LLC   
5       Santander Bank, National Association           1111 East River, Ltd.   
6                               Bank of Hope   11125 Car-Wash Partners, LLC.   
7                                Umpqua Bank  123 Business World Services, I   
8  JPMorgan Chase Bank, National Association    125 Mi Casa Restaurant Corp.   
9    Republic First Bank d/b/a Republic Bank        1450 Hospitality PA, LLC   

   GrossChargeOff ChargeOffDate  
0         33968.0       2/11/14  
1         43637.0        4/5/15  
2         70070.0        3/5/14  
3         62250.0       9/23/16  
4         38143.0        7/4/16  
5         40000.0       3/18/15  
6        224328.0       3/17/16  
7         20745.0      12/18/13  
8         22118.0        9/2/14  
9         32712.0      11/20/17

In [17]:
new_df4 = pd.merge(new_df3, new_df3b, on='BankName', how='outer')
new_df4.head(10)

BankName  TotalLoansApproval  ApprovalFiscalYear  \
0             121 Financial CU           1022000.0              2015.0   
1                    1880 Bank           2900000.0              2014.0   
2           1st Advantage Bank            140000.0              2014.0   
3                     1st Bank            463000.0              2011.0   
4                1st Bank Yuma           1115368.0              2015.0   
5           1st Bank in Hominy            938400.0              2015.0   
6             1st Capital Bank          12222700.0              2015.0   
7  1st Colonial Community Bank          31084500.0              2015.0   
8        1st Constitution Bank          72495000.0              2015.0   
9        1st Constitution Bank          72495000.0              2015.0   

                    BorrName  GrossChargeOff ChargeOffDate  
0                        NaN             NaN           NaN  
1                        NaN             NaN           NaN  
2                        NaN             NaN           NaN  
3                        NaN             NaN           NaN  
4                        NaN             NaN           NaN  
5                        NaN             NaN           NaN  
6                        NaN             NaN           NaN  
7  MALASHARD CONSULTING, LLC         72617.0       7/21/17  
8                    D&Z LLC         36904.0       3/23/16  
9             J & Me Spa Inc        249228.0        6/2/16

In [18]:
new_df4 = new_df4.dropna(subset = ['BorrName'])
new_df4.head(10)

BankName  TotalLoansApproval  ApprovalFiscalYear  \
7   1st Colonial Community Bank          31084500.0              2015.0   
8         1st Constitution Bank          72495000.0              2015.0   
9         1st Constitution Bank          72495000.0              2015.0   
12            1st MidAmerica CU             96300.0              2012.0   
15              1st Source Bank          96575260.0              2015.0   
16              1st Source Bank          96575260.0              2015.0   
17              1st Source Bank          96575260.0              2015.0   
18              1st Source Bank          96575260.0              2015.0   
19              1st Source Bank          96575260.0              2015.0   
20              1st Source Bank          96575260.0              2015.0   

                          BorrName  GrossChargeOff ChargeOffDate  
7        MALASHARD CONSULTING, LLC         72617.0       7/21/17  
8                          D&Z LLC         36904.0       3/23/16  
9                   J & Me Spa Inc        249228.0        6/2/16  
12       HUDDLE UP SPORTS INK, LTD         33995.0       9/17/14  
15  All Phase of Customized Marble         57000.0      12/11/12  
16  Audacity Employment Solutions,          7432.0       3/13/17  
17       Borzych Construction, LLC        265545.0       8/12/14  
18         Bray Construction, Inc.         39231.0      10/24/14  
19        Commercial Painters, Inc         45987.0       12/3/12  
20        Commercial Painters, Inc         13800.0        2/6/13

In [19]:
from pprint import pprint
pprint (new_df4.to_json(orient='records'))

('[{"BankName":"1st Colonial Community '
 'Bank","TotalLoansApproval":31084500.0,"ApprovalFiscalYear":2015.0,"BorrName":"MALASHARD '
 'CONSULTING, '
 'LLC","GrossChargeOff":72617.0,"ChargeOffDate":"7\\/21\\/17"},{"BankName":"1st '
 'Constitution '
 'Bank","TotalLoansApproval":72495000.0,"ApprovalFiscalYear":2015.0,"BorrName":"D&Z '
 'LLC","GrossChargeOff":36904.0,"ChargeOffDate":"3\\/23\\/16"},{"BankName":"1st '
 'Constitution '
 'Bank","TotalLoansApproval":72495000.0,"ApprovalFiscalYear":2015.0,"BorrName":"J '
 '& Me Spa '
 'Inc","GrossChargeOff":249228.0,"ChargeOffDate":"6\\/2\\/16"},{"BankName":"1st '
 'MidAmerica '
 'CU","TotalLoansApproval":96300.0,"ApprovalFiscalYear":2012.0,"BorrName":"HUDDLE '
 'UP SPORTS INK, '
 'LTD","GrossChargeOff":33995.0,"ChargeOffDate":"9\\/17\\/14"},{"BankName":"1st '
 'Source '
 'Bank","TotalLoansApproval":96575260.0,"ApprovalFiscalYear":2015.0,"BorrName":"All '
 'Phase of Customized '
 'Marble","GrossChargeOff":57000.0,"ChargeOffDate":"12\\/11\\/12"},

 'Bank, National '
 'Association","TotalLoansApproval":193852100.0,"ApprovalFiscalYear":2015.0,"BorrName":"Fuerst '
 'Consulting, '
 'Inc.","GrossChargeOff":21047.0,"ChargeOffDate":"12\\/28\\/17"},{"BankName":"Associated '
 'Bank, National '
 'Association","TotalLoansApproval":193852100.0,"ApprovalFiscalYear":2015.0,"BorrName":"Gameday '
 'Sports '
 'LLC","GrossChargeOff":116692.0,"ChargeOffDate":"6\\/30\\/16"},{"BankName":"Associated '
 'Bank, National '
 'Association","TotalLoansApproval":193852100.0,"ApprovalFiscalYear":2015.0,"BorrName":"Golden '
 'Tamarack Acquisition '
 'Co","GrossChargeOff":27544.0,"ChargeOffDate":"5\\/19\\/14"},{"BankName":"Associated '
 'Bank, National '
 'Association","TotalLoansApproval":193852100.0,"ApprovalFiscalYear":2015.0,"BorrName":"Golden '
 'Tamarack Acquisition '
 'Co","GrossChargeOff":153424.0,"ChargeOffDate":"6\\/27\\/16"},{"BankName":"Associated '
 'Bank, National '
 'Association","TotalLoansApproval":193852100.0,"ApprovalFiscalYear":2015.0,"Borr

 'of '
 'Hope","TotalLoansApproval":2667254600.0,"ApprovalFiscalYear":2015.0,"BorrName":"El '
 'Nuevo Mundo '
 'Inc.","GrossChargeOff":74725.0,"ChargeOffDate":"6\\/13\\/17"},{"BankName":"Bank '
 'of '
 'Hope","TotalLoansApproval":2667254600.0,"ApprovalFiscalYear":2015.0,"BorrName":"Fashion '
 'Spot, '
 'Inc.","GrossChargeOff":177209.0,"ChargeOffDate":"5\\/11\\/17"},{"BankName":"Bank '
 'of '
 'Hope","TotalLoansApproval":2667254600.0,"ApprovalFiscalYear":2015.0,"BorrName":"Furniture '
 '2 Go, '
 'Inc","GrossChargeOff":79445.0,"ChargeOffDate":"2\\/10\\/17"},{"BankName":"Bank '
 'of '
 'Hope","TotalLoansApproval":2667254600.0,"ApprovalFiscalYear":2015.0,"BorrName":"Furniture '
 '2 Go, '
 'Inc","GrossChargeOff":24484.0,"ChargeOffDate":"2\\/23\\/17"},{"BankName":"Bank '
 'of '
 'Hope","TotalLoansApproval":2667254600.0,"ApprovalFiscalYear":2015.0,"BorrName":"G '
 '& DY, '
 'INC.","GrossChargeOff":23142.0,"ChargeOffDate":"5\\/18\\/11"},{"BankName":"Bank '
 'of '
 'Hope","TotalLoansApproval":2

 'Company","TotalLoansApproval":788892550.0,"ApprovalFiscalYear":2015.0,"BorrName":"SANEAR '
 'CORPORATION","GrossChargeOff":13578.0,"ChargeOffDate":"3\\/10\\/14"},{"BankName":"Branch '
 'Banking and Trust '
 'Company","TotalLoansApproval":788892550.0,"ApprovalFiscalYear":2015.0,"BorrName":"SHELLBACK '
 'MECHANICAL '
 'INC","GrossChargeOff":49359.0,"ChargeOffDate":"5\\/31\\/16"},{"BankName":"Branch '
 'Banking and Trust '
 'Company","TotalLoansApproval":788892550.0,"ApprovalFiscalYear":2015.0,"BorrName":"SHELLY '
 'L TRUSSELL and ERIC K '
 'T","GrossChargeOff":8475.0,"ChargeOffDate":"12\\/13\\/13"},{"BankName":"Branch '
 'Banking and Trust '
 'Company","TotalLoansApproval":788892550.0,"ApprovalFiscalYear":2015.0,"BorrName":"SKYLINE '
 'LIGHTING '
 'INC","GrossChargeOff":251906.0,"ChargeOffDate":"9\\/14\\/15"},{"BankName":"Branch '
 'Banking and Trust '
 'Company","TotalLoansApproval":788892550.0,"ApprovalFiscalYear":2015.0,"BorrName":"SOFFAN '
 'INC","GrossChargeOff":64406.0,"ChargeOff

 'Bank '
 'Corporation","TotalLoansApproval":1432382000.0,"ApprovalFiscalYear":2015.0,"BorrName":"Siano '
 'Building Services dba '
 'Na","GrossChargeOff":52588.0,"ChargeOffDate":"9\\/29\\/15"},{"BankName":"Celtic '
 'Bank '
 'Corporation","TotalLoansApproval":1432382000.0,"ApprovalFiscalYear":2015.0,"BorrName":"Smart '
 'Tell, '
 'LLC","GrossChargeOff":73963.0,"ChargeOffDate":"3\\/1\\/18"},{"BankName":"Celtic '
 'Bank '
 'Corporation","TotalLoansApproval":1432382000.0,"ApprovalFiscalYear":2015.0,"BorrName":"Songchai '
 'LLC","GrossChargeOff":122497.0,"ChargeOffDate":"3\\/13\\/18"},{"BankName":"Celtic '
 'Bank '
 'Corporation","TotalLoansApproval":1432382000.0,"ApprovalFiscalYear":2015.0,"BorrName":"South '
 'Plains Golf Greens '
 'Texas","GrossChargeOff":135401.0,"ChargeOffDate":"5\\/8\\/17"},{"BankName":"Celtic '
 'Bank '
 'Corporation","TotalLoansApproval":1432382000.0,"ApprovalFiscalYear":2015.0,"BorrName":"Spark '
 'Print Solutions, '
 'Inc","GrossChargeOff":121535.0,"ChargeOffDat

...

 'Association","TotalLoansApproval":3422102811.0,"ApprovalFiscalYear":2015.0,"BorrName":"MICHELLE '
 'KATZ ATTORNEY AT '
 'LAW","GrossChargeOff":19843.0,"ChargeOffDate":"1\\/10\\/18"},{"BankName":"U.S. '
 'Bank National '
 'Association","TotalLoansApproval":3422102811.0,"ApprovalFiscalYear":2015.0,"BorrName":"MIDWEST '
 'MARTIAL ARTS ACADEMY '
 'I","GrossChargeOff":22005.0,"ChargeOffDate":"9\\/3\\/13"},{"BankName":"U.S. '
 'Bank National '
 'Association","TotalLoansApproval":3422102811.0,"ApprovalFiscalYear":2015.0,"BorrName":"MILLENIUM '
 'AUTO AC '
 'COMPRESSOR","GrossChargeOff":26641.0,"ChargeOffDate":"1\\/31\\/18"},{"BankName":"U.S. '
 'Bank National '
 'Association","TotalLoansApproval":3422102811.0,"ApprovalFiscalYear":2015.0,"BorrName":"MILLENIUM '
 'SPORTS MANAGEMENT, '
 'I","GrossChargeOff":19139.0,"ChargeOffDate":"1\\/8\\/18"},{"BankName":"U.S. '
 'Bank National '
 'Association","TotalLoansApproval":3422102811.0,"ApprovalFiscalYear":2015.0,"BorrName":"MILLENNIAL '
 'LANDSCAPE

 'Bank","TotalLoansApproval":958519646.0,"ApprovalFiscalYear":2015.0,"BorrName":"MILLER '
 'ELECTRIC AND '
 'TECHNOLOGY","GrossChargeOff":521091.0,"ChargeOffDate":"8\\/21\\/14"},{"BankName":"Umpqua '
 'Bank","TotalLoansApproval":958519646.0,"ApprovalFiscalYear":2015.0,"BorrName":"MONFORT '
 'DRUG COMPANY, '
 'INC.","GrossChargeOff":31512.0,"ChargeOffDate":"1\\/30\\/14"},{"BankName":"Umpqua '
 'Bank","TotalLoansApproval":958519646.0,"ApprovalFiscalYear":2015.0,"BorrName":"Ma '
 'Maison, '
 'LLC","GrossChargeOff":24402.0,"ChargeOffDate":"2\\/26\\/16"},{"BankName":"Umpqua '
 'Bank","TotalLoansApproval":958519646.0,"ApprovalFiscalYear":2015.0,"BorrName":"Mach '
 '3 Composites, '
 'LLC","GrossChargeOff":32435.0,"ChargeOffDate":"1\\/20\\/16"},{"BankName":"Umpqua '
 'Bank","TotalLoansApproval":958519646.0,"ApprovalFiscalYear":2015.0,"BorrName":"Maggie\'s '
 'General Home '
 'Cleaning","GrossChargeOff":18978.0,"ChargeOffDate":"8\\/9\\/12"},{"BankName":"Umpqua '
 'Bank","TotalLoansApproval":958

 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"Alaska '
 'Mine '
 'Services","GrossChargeOff":13435.0,"ChargeOffDate":"3\\/19\\/18"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"Alternative '
 'Health and '
 'Medical","GrossChargeOff":149114.0,"ChargeOffDate":"5\\/17\\/16"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"Alternative '
 'Health and '
 'Medical","GrossChargeOff":19768.0,"ChargeOffDate":"9\\/22\\/16"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"Alvaro '
 'Graphics '
 'LLC","GrossChargeOff":145229.0,"ChargeOffDate":"1\\/31\\/17"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"Alvaro

 'RESTORATION ASSISTED '
 'LIVI","GrossChargeOff":14788.0,"ChargeOffDate":"12\\/27\\/17"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"LIMA '
 'FIT, '
 'LLC","GrossChargeOff":13311.0,"ChargeOffDate":"1\\/18\\/18"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"LIQUID '
 'VAPOR '
 'WORLD","GrossChargeOff":14812.0,"ChargeOffDate":"9\\/24\\/15"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"LITO '
 'G '
 'GARCIA","GrossChargeOff":4471.0,"ChargeOffDate":"4\\/19\\/16"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"LJB '
 'CLIPS, '
 'LLC","GrossChargeOff":65206.0,"ChargeOffDate":"8\\/19\\/16"},{"BankName":"Wells '
 'Fargo Bank, National '
 'A

 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"THE '
 'ORIGINAL BATTERY '
 'WAREHOUSE","GrossChargeOff":27182.0,"ChargeOffDate":"10\\/14\\/16"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"THE '
 'PEEPLES DIAMONDS & '
 'COMPANY","GrossChargeOff":9827.0,"ChargeOffDate":"1\\/27\\/17"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"TIMELINE '
 'DELIVERIES, '
 'INC","GrossChargeOff":350000.0,"ChargeOffDate":"12\\/16\\/13"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"TIMUCUA '
 'TRAILS, '
 'INC","GrossChargeOff":9496.0,"ChargeOffDate":"8\\/12\\/15"},{"BankName":"Wells '
 'Fargo Bank, National '
 'Association","TotalLoansApproval":8229263704.0,"ApprovalFiscalYear":2015.0,"BorrName":"TL 

In [20]:
# new_df5 = pd.read_sql("select BankName, sum(GrossApproval), sum(GrossChargeOffAmount), SICDISCRIP, count(sic) sic_count \
# from bank_data where BankName = '%s' group by 4" % v, conn)
# new_df5.head(n=10)

In [21]:
new_df6 = pd.read_sql("select BankName, sum(GrossChargeOffAmount) as GrossChgOff, SICDISCRIP as SIC_Desr, count(SIC) SIC_count \
from bank_data where GrossChargeOffAmount > 0 group by 3 order by SIC_count desc limit 100", conn)
new_df6.head(n=10)

BankName  GrossChgOff  \
0                              PeopleFund   83154248.0   
1  Wells Fargo Bank, National Association   57386146.0   
2                            Greylock FCU    8031640.0   
3  Wells Fargo Bank, National Association   14508681.0   
4  Wells Fargo Bank, National Association    7649730.0   
5                      Bank of the Sierra   17995533.0   
6  Wells Fargo Bank, National Association   11322149.0   
7          U.S. Bank National Association   18217467.0   
8            KeyBank National Association   13658360.0   
9  Wells Fargo Bank, National Association    6092720.0   

                                            SIC_Desr  SIC_count  
0                           Full-Service Restaurants        711  
1                        Limited-Service Restaurants        502  
2  General Freight Trucking, Long Distance, Truck...        170  
3                          General Automotive Repair        161  
4                                      Beauty Salons        157  
5              All Other Specialty Trade Contractors        156  
6                             Residential Remodelers        149  
7  Plumbing, Heating, and Air-Conditioning Contra...        142  
8                               Landscaping Services        140  
9                    General Freight Trucking, Local        135

In [22]:
from pprint import pprint
pprint (new_df6.to_json(orient='records'))

('[{"BankName":"PeopleFund","GrossChgOff":83154248.0,"SIC_Desr":"Full-Service '
 'Restaurants","SIC_count":711},{"BankName":"Wells Fargo Bank, National '
 'Association","GrossChgOff":57386146.0,"SIC_Desr":"Limited-Service '
 'Restaurants","SIC_count":502},{"BankName":"Greylock '
 'FCU","GrossChgOff":8031640.0,"SIC_Desr":"General Freight Trucking, Long '
 'Distance, Truckload","SIC_count":170},{"BankName":"Wells Fargo Bank, '
 'National Association","GrossChgOff":14508681.0,"SIC_Desr":"General '
 'Automotive Repair","SIC_count":161},{"BankName":"Wells Fargo Bank, National '
 'Association","GrossChgOff":7649730.0,"SIC_Desr":"Beauty '
 'Salons","SIC_count":157},{"BankName":"Bank of the '
 'Sierra","GrossChgOff":17995533.0,"SIC_Desr":"All Other Specialty Trade '
 'Contractors","SIC_count":156},{"BankName":"Wells Fargo Bank, National '
 'Association","GrossChgOff":11322149.0,"SIC_Desr":"Residential '
 'Remodelers","SIC_count":149},{"BankName":"U.S. Bank National '
 'Association","GrossChgOf